In [9]:
from scipy.io import loadmat
import numpy as np
from sklearn.preprocessing import OneHotEncoder
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
from sklearn import metrics
import pandas as pd
import plotly.express as px

# Data Cleanup

In [3]:
mat_contents = loadmat("genomedata.mat")
raw_data = mat_contents["X"]

# get rid of all the list nesting
unnested_data = np.array([x[0][0] for x in raw_data])

# split on tab characters and remove whitespace
no_whitespace = [x.replace(" ", "") for x in unnested_data]
split_data = np.array([x.split("\t") for x in no_whitespace])

# remove last whitespace entry
clean_data = np.delete(split_data, -1, axis=1)

In [5]:
df = pd.DataFrame(clean_data)
df.head()

0    1    2    3    4    5    6    7    8    9     ... 1033 1034 1035 1036  \
0   GG   GG   GG   GG   GG   GG   GG   GG   GG   GG  ...   AA   AG   GG   GG   
1   TT   TC   TC   TC   TC   CC   CC   TT   TC   CC  ...   CC   CC   CC   TC   
2   AG   AG   AG   AG   AG   GG   GG   AA   GG   AA  ...   GG   AG   GG   AG   
3   CC   CC   TC   TC   CC   CC   TC   CC   CC   TT  ...   CC   TC   CC   CC   
4   GG   GG   GG   GG   GG   GG   AG   GG   GG   GG  ...   GG   GG   GG   GG   

  1037 1038 1039 1040 1041 1042  
0   --   GG   AG   AG   GG   AA  
1   CC   CC   CC   TC   CC   CC  
2   AG   AG   GG   AG   AG   GG  
3   TC   TC   CC   CC   TC   CC  
4   GG   GG   GG   GG   GG   GG  

[5 rows x 1043 columns]

In [6]:
# one-hot encoding
enc = OneHotEncoder(handle_unknown='ignore', sparse=False)
encoded_data = enc.fit_transform(clean_data)

encoded_data

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 1.],
       [0., 1., 0., ..., 0., 0., 0.]])

# PCA

In [7]:
pca = PCA()
pca_data = pca.fit_transform(encoded_data)

In [10]:
labels = {
    str(i): f"PC {i+1} ({var:.1f}%)"
    for i, var in enumerate(pca.explained_variance_ratio_ * 100)
}

fig = px.scatter_matrix(
    pca_data,
    labels=labels,
    dimensions=range(4)
)
fig.update_traces(diagonal_visible=False)
fig.show()

# Clustering

In [29]:
def get_scores(data, labels):
    #sillhouette score ranges from -1 to 1, where 1 is best and 0 indicates cluster overlap
    ss = metrics.silhouette_score(data, labels, metric='euclidean')
    print("Sillhouette score:", ss)
    # variance ratio criterion-- how tightly clustered (higher is better)
    chs = metrics.calinski_harabasz_score(data, labels)
    print("Calinski-Harabasz Index:", chs)
    # similarity between clusters (lower is better)
    dbs = metrics.davies_bouldin_score(data, labels)   
    print("Davies-Bouldin Index:", dbs)
    return [ss, chs, dbs]

### KNN

In [16]:
# knn clustering
clusterer = KMeans(n_clusters=10)
sk_labels = clusterer.fit_predict(pca_data)

In [30]:
ss, chs, dbs = get_scores(pca_data, sk_labels)

Sillhouette score: 0.39615005953473054
Calinski-Harabasz Index: 4715.921713553987
Davies-Bouldin Index: 0.8321511080983444


In [31]:
number_of_components = []
sillhouette = []
calinski = []
davies = []

In [32]:
# testing out how PCA works for different num components
components = [10, 20, 40, 100]
for num_components in components:
    pca = PCA(n_components = num_components)
    pca_data = pca.fit_transform(encoded_data)
    print("Number of components:", num_components)
    
    clusterer = KMeans(n_clusters=10)
    sk_labels = clusterer.fit_predict(pca_data)
    ss, chs, dbs = get_scores(pca_data, sk_labels)
    number_of_components.append(num_components)
    sillhouette.append(ss)
    calinski.append(chs)
    davies.append(dbs)
    print("\n")

Number of components: 10
Sillhouette score: 0.39624084405422044
Calinski-Harabasz Index: 4716.767092923844
Davies-Bouldin Index: 0.833200595020468


Number of components: 20
Sillhouette score: 0.3175956884262429
Calinski-Harabasz Index: 3073.172989797203
Davies-Bouldin Index: 1.0733809706881037


Number of components: 40
Sillhouette score: 0.28593267074784223
Calinski-Harabasz Index: 2477.98681733497
Davies-Bouldin Index: 1.2279517508377005


Number of components: 100
Sillhouette score: 0.24369488322623548
Calinski-Harabasz Index: 1752.242941379511
Davies-Bouldin Index: 1.495331482062037




In [33]:
components = [1, 2, 3, 5, 8]
for num_components in components:
    pca = PCA(n_components = num_components)
    pca_data = pca.fit_transform(encoded_data)
    print("Number of components:", num_components)
    
    clusterer = KMeans(n_clusters=10)
    sk_labels = clusterer.fit_predict(pca_data)
    ss, chs, dbs = get_scores(pca_data, sk_labels)
    number_of_components.append(num_components)
    sillhouette.append(ss)
    calinski.append(chs)
    davies.append(dbs)
    print("\n")

Number of components: 1
Sillhouette score: 0.5768240860722983
Calinski-Harabasz Index: 107744.95268634833
Davies-Bouldin Index: 0.5025942635730187


Number of components: 2
Sillhouette score: 0.5380137268794943
Calinski-Harabasz Index: 19379.184797903374
Davies-Bouldin Index: 0.5476486225982699


Number of components: 3
Sillhouette score: 0.5482862560305987
Calinski-Harabasz Index: 14070.115262139936
Davies-Bouldin Index: 0.5386000558503501


Number of components: 5
Sillhouette score: 0.5119798847613458
Calinski-Harabasz Index: 8810.30960214854
Davies-Bouldin Index: 0.5875097261312786


Number of components: 8
Sillhouette score: 0.44800853334835283
Calinski-Harabasz Index: 6125.252299327524
Davies-Bouldin Index: 0.6985353410864962




In [36]:
pca_analysis = {"Number of Components": number_of_components, "Sillhouette Score": sillhouette, "Calinski-Harabasz Index": calinski, "Davies-Bouldin Index": davies}
pca_df = pd.DataFrame(pca_analysis)
pca_df.head()

Number of Components  Sillhouette Score  Calinski-Harabasz Index  \
0                    10           0.396241              4716.767093   
1                    20           0.317596              3073.172990   
2                    40           0.285933              2477.986817   
3                   100           0.243695              1752.242941   
4                     1           0.576824            107744.952686   

   Davies-Bouldin Index  
0              0.833201  
1              1.073381  
2              1.227952  
3              1.495331  
4              0.502594

In [40]:
fig = px.scatter(pca_df, x="Number of Components", y="Sillhouette Score")
fig.show()

In [41]:
fig = px.scatter(pca_df, x="Number of Components", y="Calinski-Harabasz Index")
fig.show()

In [42]:
fig = px.scatter(pca_df, x="Number of Components", y="Davies-Bouldin Index")
fig.show()